In [2]:
!pip install tensorflow_gpu==1.15

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
!pip install numpy==1.19.5
!pip uninstall -y pycocotools
!pip install pycocotools --no-binary pycocotools

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Found existing installation: pycocotools 2.0.4
Uninstalling pycocotools-2.0.4:
  Successfully uninstalled pycocotools-2.0.4
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached pycocotools-2.0.4.tar.gz (106 kB)
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for pycocotools: filename=pycocotools-2.0.4-cp37-cp37m-linux_x86_64.whl size=265197 sha256=9570a54c700a3621a0f7eebc6df93d3a23bc8039c24d727fe14be195f85c9085
  Stored in directory: /root/.cache/pip/wheels/a3/5f/fa/f011e578cc76e1fc5be8dce30b3eb9fd00f337e744b3bba59b
Successfully built pycocotools


In [4]:
%tensorflow_version 1.x #for obj
from google.colab import drive
drive.mount('/content/drive')

`%tensorflow_version` only switches the major version: 1.x or 2.x.
You set: `1.x #for obj`. This will be interpreted as: `1.x`.


TensorFlow 1.x selected.
Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [5]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [6]:
#checking GPU
!nvidia-smi -L

GPU 0: Tesla T4 (UUID: GPU-c60a66aa-078c-4aa1-5936-3ba2e0bba7ba)


# 0. Setup Paths

In [7]:
import os

In [8]:
CUSTOM_MODEL_NAME = 'ssd_inception_v2' 
PRETRAINED_MODEL_NAME = 'ssd_inception_v2_coco_2018_01_28'
PRETRAINED_MODEL_URL = 'http://download.tensorflow.org/models/object_detection/ssd_inception_v2_coco_2018_01_28.tar.gz'
TF_RECORD_SCRIPT_NAME = 'generate_tfrecord.py'
LABEL_MAP_NAME = 'label_map.pbtxt'

In [9]:
paths = {
    'WORKSPACE_PATH': os.path.join('Tensorflow', 'workspace'),
    'SCRIPTS_PATH': os.path.join('Tensorflow','scripts'),
    'APIMODEL_PATH': os.path.join('Tensorflow','models'),
    'ANNOTATION_PATH': os.path.join('Tensorflow', 'workspace','annotations'),
    'IMAGE_PATH': os.path.join('Tensorflow', 'workspace','images'),
    'MODEL_PATH': os.path.join('Tensorflow', 'workspace','models'),
    'PRETRAINED_MODEL_PATH': os.path.join('Tensorflow', 'workspace','pre-trained-models'),
    'CHECKPOINT_PATH': os.path.join('Tensorflow', 'workspace','models',CUSTOM_MODEL_NAME), 
    'OUTPUT_PATH': os.path.join('Tensorflow', 'workspace','models',CUSTOM_MODEL_NAME, 'export'), 
    'TFJS_PATH':os.path.join('Tensorflow', 'workspace','models',CUSTOM_MODEL_NAME, 'tfjsexport'), 
    'TFLITE_PATH':os.path.join('Tensorflow', 'workspace','models',CUSTOM_MODEL_NAME, 'tfliteexport'), 
    'PROTOC_PATH':os.path.join('Tensorflow','protoc')
 }

In [10]:
files = {
    'PIPELINE_CONFIG':os.path.join('Tensorflow', 'workspace','models', CUSTOM_MODEL_NAME, 'pipeline.config'),
    'TF_RECORD_SCRIPT': os.path.join(paths['SCRIPTS_PATH'], TF_RECORD_SCRIPT_NAME), 
    'LABELMAP': os.path.join(paths['ANNOTATION_PATH'], LABEL_MAP_NAME)
}

In [11]:
for path in paths.values():
    if not os.path.exists(path):
        if os.name == 'posix':
            !mkdir -p {path}
        if os.name == 'nt':
            !mkdir {path}

# 1. Download TF Models Pretrained Models from Tensorflow Model Zoo and Install TFOD

In [12]:
# https://www.tensorflow.org/install/source_windows

In [13]:
if os.name=='nt':
    !pip install wget
    import wget

In [14]:
!pip install wget

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [15]:
if not os.path.exists(os.path.join(paths['APIMODEL_PATH'], 'research', 'object_detection')):
    !git clone https://github.com/tensorflow/models {paths['APIMODEL_PATH']}

In [16]:
# Install Tensorflow Object Detection 
if os.name=='posix':  
    !apt-get install protobuf-compiler
    !cd Tensorflow/models/research && protoc object_detection/protos/*.proto --python_out=. && cp object_detection/packages/tf1/setup.py . && python -m pip install . 
    
if os.name=='nt':
    url="https://github.com/protocolbuffers/protobuf/releases/download/v3.15.6/protoc-3.15.6-win64.zip"
    wget.download(url)
    !move protoc-3.15.6-win64.zip {paths['PROTOC_PATH']}
    !cd {paths['PROTOC_PATH']} && tar -xf protoc-3.15.6-win64.zip
    os.environ['PATH'] += os.pathsep + os.path.abspath(os.path.join(paths['PROTOC_PATH'], 'bin'))   
    !cd Tensorflow/models/research && protoc object_detection/protos/*.proto --python_out=. && copy object_detection\\packages\\tf1\\setup.py setup.py && python setup.py build && python setup.py install
    !cd Tensorflow/models/research/slim && pip install -e . 

Reading package lists... Done
Building dependency tree       
Reading state information... Done
protobuf-compiler is already the newest version (3.0.0-9.1ubuntu1).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 41 not upgraded.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Processing /content/Tensorflow/models/research
  DEPRECATION: A future pip version will change local packages to be built in-place without first copying to a temporary directory. We recommend you use --use-feature=in-tree-build to test your packages with this new behavior before it becomes the default.
   pip 21.3 will remove support for this functionality. You can find discussion regarding this at https://github.com/pypa/pip/issues/7555.
  Created wheel for object-detection: filename=object_detection-0.1-py3-none-any.whl size=16924

In [17]:
VERIFICATION_SCRIPT = os.path.join(paths['APIMODEL_PATH'], 'research', 'object_detection', 'builders', 'model_builder_tf1_test.py')
# Verify Installation
!python {VERIFICATION_SCRIPT}

Using TensorFlow backend.
Running tests under Python 3.7.13: /usr/bin/python3
[ RUN      ] ModelBuilderTF1Test.test_create_context_rcnn_from_config_with_params0 (True)
[       OK ] ModelBuilderTF1Test.test_create_context_rcnn_from_config_with_params0 (True)
[ RUN      ] ModelBuilderTF1Test.test_create_context_rcnn_from_config_with_params1 (False)
[       OK ] ModelBuilderTF1Test.test_create_context_rcnn_from_config_with_params1 (False)
[ RUN      ] ModelBuilderTF1Test.test_create_experimental_model
[       OK ] ModelBuilderTF1Test.test_create_experimental_model
[ RUN      ] ModelBuilderTF1Test.test_create_faster_rcnn_from_config_with_crop_feature0 (True)
[       OK ] ModelBuilderTF1Test.test_create_faster_rcnn_from_config_with_crop_feature0 (True)
[ RUN      ] ModelBuilderTF1Test.test_create_faster_rcnn_from_config_with_crop_feature1 (False)
[       OK ] ModelBuilderTF1Test.test_create_faster_rcnn_from_config_with_crop_feature1 (False)
[ RUN      ] ModelBuilderTF1Test.test_create_faste

In [18]:
import object_detection

In [19]:
if os.name =='posix':
    !wget {PRETRAINED_MODEL_URL}
    !mv {PRETRAINED_MODEL_NAME+'.tar.gz'} {paths['PRETRAINED_MODEL_PATH']}
    !cd {paths['PRETRAINED_MODEL_PATH']} && tar -zxvf {PRETRAINED_MODEL_NAME+'.tar.gz'}
if os.name == 'nt':
    wget.download(PRETRAINED_MODEL_URL)
    !move {PRETRAINED_MODEL_NAME+'.tar.gz'} {paths['PRETRAINED_MODEL_PATH']}
    !cd {paths['PRETRAINED_MODEL_PATH']} && tar -zxvf {PRETRAINED_MODEL_NAME+'.tar.gz'}

--2022-05-25 16:30:43--  http://download.tensorflow.org/models/object_detection/ssd_inception_v2_coco_2018_01_28.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 74.125.195.128, 2607:f8b0:400e:c02::80
Connecting to download.tensorflow.org (download.tensorflow.org)|74.125.195.128|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 278114232 (265M) [application/x-tar]
Saving to: ‘ssd_inception_v2_coco_2018_01_28.tar.gz’

ssd_inception_v2_co 100%[===================>] 265.23M   380MB/s    in 0.7s    

2022-05-25 16:30:44 (380 MB/s) - ‘ssd_inception_v2_coco_2018_01_28.tar.gz’ saved [278114232/278114232]

ssd_inception_v2_coco_2018_01_28/
ssd_inception_v2_coco_2018_01_28/model.ckpt.index
ssd_inception_v2_coco_2018_01_28/checkpoint
ssd_inception_v2_coco_2018_01_28/pipeline.config
ssd_inception_v2_coco_2018_01_28/model.ckpt.data-00000-of-00001
ssd_inception_v2_coco_2018_01_28/model.ckpt.meta
ssd_inception_v2_coco_2018_01_28/saved_model/
ssd_inception_

# 2. Create Label Map

In [20]:
labels = [{'name':'knife', 'id':1}, {'name':'pistol', 'id':2}]

with open(files['LABELMAP'], 'w') as f:
    for label in labels:
        f.write('item { \n')
        f.write('\tname:\'{}\'\n'.format(label['name']))
        f.write('\tid:{}\n'.format(label['id']))
        f.write('}\n')

# 3. Create TF records

In [20]:
!tar -xvf /content/drive/MyDrive/Thesis_gun_detection/weapon_data/weapon_dataset_main.tar.gz -C /content/Tensorflow/workspace/

Streaming output truncated to the last 5000 lines.
images/train/armas--925-_jpg.rf.2af81b8bde1c83fafc914975a8ad89b2.xml
images/train/armas--926-_jpg.rf.db5f530fdff872a1b1e7a90989290db3.jpg
images/train/armas--926-_jpg.rf.db5f530fdff872a1b1e7a90989290db3.xml
images/train/armas--927-_jpg.rf.5321344f9801b9daed6d460c0fa9f656.jpg
images/train/armas--927-_jpg.rf.5321344f9801b9daed6d460c0fa9f656.xml
images/train/armas--928-_jpg.rf.d6dc3e35cd2d6930d4847c0f4d501af1.jpg
images/train/armas--928-_jpg.rf.d6dc3e35cd2d6930d4847c0f4d501af1.xml
images/train/armas--929-_jpg.rf.98babb96d1b7d3f5cf03f7d55c7859f6.jpg
images/train/armas--929-_jpg.rf.98babb96d1b7d3f5cf03f7d55c7859f6.xml
images/train/armas--93-_jpg.rf.46a9313af59c0d66cb92aec43b6b18f7.jpg
images/train/armas--93-_jpg.rf.46a9313af59c0d66cb92aec43b6b18f7.xml
images/train/armas--930-_jpg.rf.dcf2b0baef36d518fb15174a641b6804.jpg
images/train/armas--930-_jpg.rf.dcf2b0baef36d518fb15174a641b6804.xml
images/train/armas--931-_jpg.rf.aaa8832368707358628f68

In [21]:
!pip uninstall opencv-python-headless==4.5.5.62
!pip install opencv-python-headless==4.5.2.52

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 38.2 MB 1.2 MB/s 


In [21]:
import cv2

In [22]:
#checking images validity 
from pathlib import Path
import imghdr

def check_images_extensions(directory):

    data_dir = directory
    image_extensions = [".png", ".jpg"]  # add there all your images file extensions

    img_type_accepted_by_tf = ["bmp", "gif", "jpeg", "png"]
    for filepath in Path(data_dir).rglob("*"):
        if filepath.suffix.lower() in image_extensions:
            img_type = imghdr.what(filepath)
            if img_type is None:
                print(f"{filepath} is not an image")

                img = cv2.imread(str(filepath))
                cv2.imwrite(str(filepath), img, [int(cv2.IMWRITE_JPEG_QUALITY), 100])

            elif img_type not in img_type_accepted_by_tf:
                print(f"{filepath} is a {img_type}, not accepted by TensorFlow")
                img = cv2.imread(str(filepath))
                cv2.imwrite(str(filepath), img, [int(cv2.IMWRITE_JPEG_QUALITY), 100])

check_images_extensions('/content/Tensorflow/workspace/images/train')
check_images_extensions('/content/Tensorflow/workspace/images/test')

In [24]:
# # OPTIONAL IF RUNNING ON COLAB
# ARCHIVE_FILES = os.path.join(paths['IMAGE_PATH'], 'archive.tar.gz')
# if os.path.exists(ARCHIVE_FILES):
#   !tar -zxvf {ARCHIVE_FILES}

In [25]:
if not os.path.exists(files['TF_RECORD_SCRIPT']):
    !git clone https://github.com/nicknochnack/GenerateTFRecord {paths['SCRIPTS_PATH']}

Cloning into 'Tensorflow/scripts'...
remote: Enumerating objects: 3, done.
remote: Counting objects: 100% (3/3), done.
remote: Compressing objects: 100% (2/2), done.
remote: Total 3 (delta 0), reused 1 (delta 0), pack-reused 0
Unpacking objects: 100% (3/3), done.


In [23]:
files

{'LABELMAP': 'Tensorflow/workspace/annotations/label_map.pbtxt',
 'PIPELINE_CONFIG': 'Tensorflow/workspace/models/ssd_inception_v2/pipeline.config',
 'TF_RECORD_SCRIPT': 'Tensorflow/scripts/generate_tfrecord.py'}

In [28]:
!python {files['TF_RECORD_SCRIPT']} -x {'/content/Tensorflow/workspace/images/train'} -l {files['LABELMAP']} -o {os.path.join(paths['ANNOTATION_PATH'], 'train.record')} 
!python {files['TF_RECORD_SCRIPT']} -x {'/content/Tensorflow/workspace/images/test'} -l {files['LABELMAP']} -o {os.path.join(paths['ANNOTATION_PATH'], 'test.record')} 

Successfully created the TFRecord file: Tensorflow/workspace/annotations/train.record
Successfully created the TFRecord file: Tensorflow/workspace/annotations/test.record


# 4. Copy Model Config to Training Folder

In [36]:
if os.name =='posix':
    !cp {os.path.join(paths['PRETRAINED_MODEL_PATH'], PRETRAINED_MODEL_NAME, 'pipeline.config')} {os.path.join(paths['CHECKPOINT_PATH'])}
if os.name == 'nt':
    !copy {os.path.join(paths['PRETRAINED_MODEL_PATH'], PRETRAINED_MODEL_NAME, 'pipeline.config')} {os.path.join(paths['CHECKPOINT_PATH'])}

# 5. Update Config For Transfer Learning

In [37]:
import tensorflow as tf
from object_detection.utils import config_util
from object_detection.protos import pipeline_pb2
from google.protobuf import text_format

In [38]:
config = config_util.get_configs_from_pipeline_file(files['PIPELINE_CONFIG'])

In [39]:
config

{'eval_config': num_examples: 8000
 max_evals: 10
 use_moving_averages: false,
 'eval_input_config': label_map_path: "PATH_TO_BE_CONFIGURED/mscoco_label_map.pbtxt"
 shuffle: false
 num_readers: 1
 tf_record_input_reader {
   input_path: "PATH_TO_BE_CONFIGURED/mscoco_val.record"
 },
 'eval_input_configs': [label_map_path: "PATH_TO_BE_CONFIGURED/mscoco_label_map.pbtxt"
 shuffle: false
 num_readers: 1
 tf_record_input_reader {
   input_path: "PATH_TO_BE_CONFIGURED/mscoco_val.record"
 }
 ],
 'model': ssd {
   num_classes: 90
   image_resizer {
     fixed_shape_resizer {
       height: 300
       width: 300
     }
   }
   feature_extractor {
     type: "ssd_inception_v2"
     depth_multiplier: 1.0
     min_depth: 16
     conv_hyperparams {
       regularizer {
         l2_regularizer {
           weight: 3.9999998989515007e-05
         }
       }
       initializer {
         truncated_normal_initializer {
           mean: 0.0
           stddev: 0.029999999329447746
         }
       }
    

In [40]:
pipeline_config = pipeline_pb2.TrainEvalPipelineConfig()
with tf.io.gfile.GFile(files['PIPELINE_CONFIG'], "r") as f:                                                                                                                                                                                                                     
    proto_str = f.read()                                                                                                                                                                                                                                          
    text_format.Merge(proto_str, pipeline_config) 

In [41]:
pipeline_config.model.ssd.num_classes = len(labels)
pipeline_config.train_config.batch_size = 32
pipeline_config.train_config.fine_tune_checkpoint = os.path.join(paths['PRETRAINED_MODEL_PATH'], PRETRAINED_MODEL_NAME, 'checkpoint', 'ckpt-0')
pipeline_config.train_config.fine_tune_checkpoint_type = "detection"
pipeline_config.train_input_reader.label_map_path= files['LABELMAP']
pipeline_config.train_input_reader.tf_record_input_reader.input_path[:] = [os.path.join(paths['ANNOTATION_PATH'], 'train.record')]
pipeline_config.eval_input_reader[0].label_map_path = files['LABELMAP']
pipeline_config.eval_input_reader[0].tf_record_input_reader.input_path[:] = [os.path.join(paths['ANNOTATION_PATH'], 'test.record')]

In [42]:
config_text = text_format.MessageToString(pipeline_config)                                                                                                                                                                                                        
with tf.io.gfile.GFile(files['PIPELINE_CONFIG'], "wb") as f:                                                                                                                                                                                                                     
    f.write(config_text) 

# 6. Train the model

In [50]:
TRAINING_SCRIPT = os.path.join(paths['APIMODEL_PATH'], 'research', 'object_detection', 'model_main.py')

In [51]:
command = "python {} --model_dir={} --pipeline_config_path={} --num_train_steps=10000".format(TRAINING_SCRIPT, paths['CHECKPOINT_PATH'],files['PIPELINE_CONFIG'])

In [52]:
print(command)

python Tensorflow/models/research/object_detection/model_main.py --model_dir=Tensorflow/workspace/models/ssd_inception_v2 --pipeline_config_path=Tensorflow/workspace/models/ssd_inception_v2/pipeline.config --num_train_steps=10000


In [53]:
!apt install --allow-change-held-packages libcudnn8=8.1.0.77-1+cuda11.2

Reading package lists... Done
Building dependency tree       
Reading state information... Done
libcudnn8 is already the newest version (8.1.0.77-1+cuda11.2).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 40 not upgraded.


In [54]:
!{command}

Using TensorFlow backend.
W0525 17:25:47.458274 139900695865216 model_lib.py:839] Forced number of epochs for all eval validations to be 1.
INFO:tensorflow:Maybe overwriting train_steps: 10000
I0525 17:25:47.458483 139900695865216 config_util.py:552] Maybe overwriting train_steps: 10000
INFO:tensorflow:Maybe overwriting use_bfloat16: False
I0525 17:25:47.458581 139900695865216 config_util.py:552] Maybe overwriting use_bfloat16: False
INFO:tensorflow:Maybe overwriting sample_1_of_n_eval_examples: 1
I0525 17:25:47.458663 139900695865216 config_util.py:552] Maybe overwriting sample_1_of_n_eval_examples: 1
INFO:tensorflow:Maybe overwriting eval_num_epochs: 1
I0525 17:25:47.458740 139900695865216 config_util.py:552] Maybe overwriting eval_num_epochs: 1
W0525 17:25:47.458840 139900695865216 model_lib.py:855] Expected number of evaluation epochs is 1, but instead encountered `eval_on_train_input_config.num_epochs` = 0. Overwriting `num_epochs` to 1.
INFO:tensorflow:create_estimator_and_inputs

# 7. Evaluate the Model

In [55]:
command = "python {} --model_dir={} --pipeline_config_path={} --checkpoint_dir={}".format(TRAINING_SCRIPT, paths['CHECKPOINT_PATH'],files['PIPELINE_CONFIG'], paths['CHECKPOINT_PATH'])

In [56]:
print(command)

python Tensorflow/models/research/object_detection/model_main.py --model_dir=Tensorflow/workspace/models/ssd_inception_v2 --pipeline_config_path=Tensorflow/workspace/models/ssd_inception_v2/pipeline.config --checkpoint_dir=Tensorflow/workspace/models/ssd_inception_v2


In [57]:
!{command}

Using TensorFlow backend.
W0525 18:20:39.185700 140198493505408 model_lib.py:839] Forced number of epochs for all eval validations to be 1.
INFO:tensorflow:Maybe overwriting train_steps: None
I0525 18:20:39.185899 140198493505408 config_util.py:552] Maybe overwriting train_steps: None
INFO:tensorflow:Maybe overwriting use_bfloat16: False
I0525 18:20:39.185982 140198493505408 config_util.py:552] Maybe overwriting use_bfloat16: False
INFO:tensorflow:Maybe overwriting sample_1_of_n_eval_examples: 1
I0525 18:20:39.186079 140198493505408 config_util.py:552] Maybe overwriting sample_1_of_n_eval_examples: 1
INFO:tensorflow:Maybe overwriting eval_num_epochs: 1
I0525 18:20:39.186160 140198493505408 config_util.py:552] Maybe overwriting eval_num_epochs: 1
W0525 18:20:39.186257 140198493505408 model_lib.py:855] Expected number of evaluation epochs is 1, but instead encountered `eval_on_train_input_config.num_epochs` = 0. Overwriting `num_epochs` to 1.
INFO:tensorflow:create_estimator_and_inputs: 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



0\x86\xef\xef\xefa\x91\n\xf4\xc8I*\xfa\x8e\\K\x12\x86F\xea3\xeeJef\xa0\xc6-\x8cj\x99\x01\xdc\x81\x87\xc7\xa2D\xbb\xf5\xc6\x9br\xc6\\\xc9(J%=\x10\xad\xc4\xfa\xfa\x1af\xdb\xdd\x95K\xd8?\x12\t<*\xdc\xfak\xaaH\xff\xa64Z\xba&\xb7\xe3\xf2U\xa54\xbfs\xf7\xaeM\xaf\x80\x1aZ\xeb`\x94d\x01\xd5\xd9\x07\x07P\x19\xd8e\xfe\xcd7\xdf\xc4"x\xd3[\xa0vI\x12u\x9a_\xfb\x95_\xb1\xe9\x1f\xfd\xe8g6\xfdW?\xfe)T\xcc+\xe0]P=wz\xe2\xbb\x1a\xa2\xe3H9\xb6\x93\xad\x86\x02zA"\x15\xd0\xbe\xfaG\x8a4k\xe8\xac\x03\xd9\xf0\xa4(\xe4\xa9\xd1\x98\xf5\xf0\x1d\xb9\xc6\xb5,^\xc9%>A\xcb\xe5<\xeb\x07\xcf\x1el\x8d\xc0\n\x00\x14\xa9\x9d\xab\xbb\x19I\r\xa5?!d\x11\xbc\x02d?\x18n\xbc\xa4&\x96\xa3\xe1H\xe5\x9c\xe5\x94\xd6g\xbc4\x80D\x8d\x81XOG\xa9m\x89\\ \xe5\x08\xa5}/\xeb\xc8U\\\x93\x89,\xdf\x1c\x8dd\xb9\xa1S\xc9K\x97d\xc1h\xbb-1\x91SI\xac\xdbt*\x01\xcep8\xb6\xe9\xc1@\xad^=<\x14\xd9\xf5x,\xd9.]\xba\x84\xd90\xc6\xc4\xba\xe1%\xdb\x10\x8f\xf1\xef3\x18\xff2\xfe\xc5l\x8c\x7f}\x95a\xfc[\xe3\'_6\xc6\xbf\xbe\xca\x9c\xab\x88\x89!\x0f\xc2\xf8\xf

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



,\xa1;\xd7\xa5\xe4\xff~9)\xffW\xfe/\x1b#\xff\xb7{\xa0\xfc_\xf9\xbf\xf2\x7f\x135\xcb\xffM\x15\x97\xff\xcbl\xf2\x7f\xbb\xb4\xfc_\xf9\xbf\xa9\x9f\\\xfb\xe5\xff&\xbe\x97\xff{\xd7\xfc\xdf \x08\x82 \x08\x82 \x08\x82 \x08\x82 \x08\x82 \x08\x82 \x08\x82 \xdc\x17\xe8\xcd\xe5C\xa5\xee^\xe6\xdf\xe6!M\xd1\x8a\xb0d6\xa2I0\xa0kGK\x0c\x15H\x19\x97\xae\xd8?\xea\x8f\x9e>\xdd\xa5G\xfe_\xf4\t\xb8T9X\xcfLg\xfd\xe8\x92vK\xf7\xf1a\xd8\xb8\xbf\xde\x0b\xd0a\x1f;\xf3@\x97~\xe5ec\x1b}\xfa7?\xcd"/>\xff\xa2\xb5\xb3o\xed|\xf4\x89\xc7\x99\xed\xec\xf9s]\xfa\xfc\xc3\xf6\xf7~\x0f\xac\xa2\xcc\xf3\x0b\xf2\xd6x(d\xa4\xb4\t\x8aY\xf0l\x97\x024\xe7\xa3\xa3#f\x9bN\x8dU\xb4\xb1a\xfc\x88\x1ct\xf2\x05\x97Ws\x02\x94\x9etL\x8a\x04y4\x19F\x99d\xe4\xe0y\x10l\xd8\xb5k\xd7\xe6~\x1f<\x8fcm8\x9a\xfb\xf4\x10B\x03v3\'\x00\x19R\xe3\xe9\x84E\xd8f\xd66\x08\x8e\xe0\xd3\x9bb\x11Y7\x87\t(Z\xbbG\x8eU\xb4:d\r\xe0[\x81\xb0\xd6\xb4\x8eyT%\xfa9Z\xc2\x15\xa8L\x8e\xc8\x92%)\x93|M\xdex\xdfz"J\x0b\xa6v\x9b[\xfb\xc9\xa0\xcf+\xd7\xe6~\x0f\xe4n\xb2l\x91\x

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



]\x16m\xf56|l\x7f\xf0\xf0\x11&\x1b\x82j\xfbJ&\xf6\x00\xa4\xb5k\x17\xd61\xcb\xebo\xbc\xee\xedo\x7f\xe7;\xde\xfe\xdaW\xbe\x8a\xc9p\xf7\xe9\x95\x15i\xccp$\x02\x81\x9e\x16\x1d\x8f\'"\xee\xae\x81f9\x83\x86u\xfb=\xcc\xb2\x0f\xbbR\xe3\x16\xd3\xcd\x86\xd2\x17\xac,\x88\xd4\x1d\xc4\xc4\xae\xdb\x15E\xc3`\xa4\xfa|\x00\n\xe2\xdd\x1e\xf4\xb3\x96\x1f\x8c\xe0\xa2\x8f\xa1\xe8!(\'&ZT2V\nh\x10>\x80\xa8g\x1c(\xa0\xe1r\xe4\xf5Fi\x16\xe7\\\xbf\x90\x92\xc7\xd8N{+\xf7\n\xd2\x15\x8bD\x05tV\xaf \x07N\x13J\x03\x11\x85N\xaa\xec\xda\xfc\x7f\x96\x8a\xcb)\xc5S\x87\xd2\x94\x9ff\xfa\xda\x919\x10\xe8\xc4-\xbd\x0f\x12\x9e\xe6\xec\xd4oA\x8d\x96\x82\xf84\x93r\x0b\x1f\x9f\x02:\xb1d5\xe9\x8d\xd4\xb4\x9fr\x0b\x07\xd7b\xfe\xe2\xf4\n\x9c\x15-\xe4lI:\xcd\xb3\xaf\x80&\xf3G_\xcd\x13V\xa0[o\x14\xc1\x0c||\xcbPN\x15)\xcf\xa0@\x1a\x8cO\x81\xc8\xfa\xa4\xfd}y\xf7F\xd1\xf1\xc2\x82xUKKK\x98\x05\xd5\xcd\xa8zF\xd11\x8a\x91\x03,\x01u\xa4\x9dX\x0b:>N\xafqD\x9d\xf5\xf2\xf2\xb23\xc0\x92\xb13#mv\xf4\x7f\xe9\xff\xd2\xff\xa5\xff\xfb)\xf4\x7f\xe9\

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# 8. Load Train Model From Checkpoint

In [ ]:
import os
import tensorflow as tf
from object_detection.utils import label_map_util
from object_detection.utils import visualization_utils as viz_utils
from object_detection.builders import model_builder
from object_detection.utils import config_util

Using TensorFlow backend.


In [ ]:
paths['CHECKPOINT_PATH']

'Tensorflow/workspace/models/ssd_inception_v2'

In [ ]:
# Load pipeline config and build a detection model
configs = config_util.get_configs_from_pipeline_file(files['PIPELINE_CONFIG'])
detection_model = model_builder.build(model_config=configs['model'], is_training=False)

# Restore checkpoint
ckpt = tf.compat.v2.train.Checkpoint(model=detection_model)
ckpt.restore(os.path.join(paths['CHECKPOINT_PATH'], 'model.ckpt-5000')).expect_partial()

@tf.function
def detect_fn(image):
    image, shapes = detection_model.preprocess(image)
    prediction_dict = detection_model.predict(image, shapes)
    detections = detection_model.postprocess(prediction_dict, shapes)
    return detections

Instructions for updating:
Restoring a name-based tf.train.Saver checkpoint using the object-based restore API. This mode uses global names to match variables, and so is somewhat fragile. It also adds new restore ops to the graph each time it is called when graph building. Prefer re-encoding training checkpoints in the object-based format: run save() on the object-based saver (the same one this message is coming from) and use that checkpoint in the future.
Instructions for updating:
If using Keras pass *_constraint arguments to layers.


# 9. Detect from an Image

In [ ]:
import cv2 
import numpy as np
from matplotlib import pyplot as plt
%matplotlib inline

In [ ]:
category_index = label_map_util.create_category_index_from_labelmap(files['LABELMAP'])

In [ ]:
def detect_weapon(img_path):
    IMAGE_PATH=img_path
    img = cv2.imread(IMAGE_PATH)
    image_np = np.array(img)

    input_tensor = tf.convert_to_tensor(np.expand_dims(image_np, 0), dtype=tf.float32)
    detections = detect_fn(input_tensor)

    num_detections = int(detections.pop('num_detections'))
    detections = {key: value[0, :num_detections].numpy()
                  for key, value in detections.items()}
    detections['num_detections'] = num_detections

    # detection_classes should be ints.
    detections['detection_classes'] = detections['detection_classes'].astype(np.int64)

    label_id_offset = 1
    image_np_with_detections = image_np.copy()

    viz_utils.visualize_boxes_and_labels_on_image_array(
                image_np_with_detections,
                detections['detection_boxes'],
                detections['detection_classes']+label_id_offset,
                detections['detection_scores'],
                category_index,
                use_normalized_coordinates=True,
                max_boxes_to_draw=5,
                min_score_thresh=.8,
                agnostic_mode=False)
    plt.figure(figsize=(20,20),dpi=100)
    plt.imshow(cv2.cvtColor(image_np_with_detections, cv2.COLOR_BGR2RGB))
    plt.show()

In [61]:
!tensorboard dev upload --logdir = /content/Tensorflow/workspace/models/ssd_inception_v2/eval_0

usage: tensorboard [-h] [--helpfull] [--logdir PATH] [--host ADDR]
                   [--port PORT] [--purge_orphaned_data BOOL] [--db URI]
                   [--db_import] [--inspect] [--version_tb] [--tag TAG]
                   [--event_file PATH] [--path_prefix PATH]
                   [--window_title TEXT] [--max_reload_threads COUNT]
                   [--reload_interval SECONDS] [--reload_task TYPE]
                   [--reload_multifile BOOL]
                   [--reload_multifile_inactive_secs SECONDS]
                   [--generic_data TYPE]
                   [--samples_per_plugin SAMPLES_PER_PLUGIN]
                   [--debugger_data_server_grpc_port PORT]
                   [--debugger_port PORT] [--master_tpu_unsecure_channel ADDR]
                   [--whatif-use-unsafe-custom-prediction YOUR_CUSTOM_PREDICT_FUNCTION.py]
                   [--whatif-data-dir PATH]
tensorboard: error: unrecognized arguments: dev upload /content/Tensorflow/workspace/models/ssd_inception_v2

In [ ]:
detect_weapon('/content/Tensorflow/workspace/images/test/12-brad-INGLOURIOUS-B-415_jpg.rf.43d9080d949b422c94f51a946cfd67fe.jpg')

Instructions for updating:
Please use `layer.__call__` method instead.
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
INFO:tensorflow:depth of additional conv before box predictor: 0
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


ValueError: ignored